Cedar River National Grassland example

In [50]:
# Import packages used for the analysis
import os
from glob import glob

import earthpy as et
import earthpy.appeears as eaapp
import geopandas as gpd
import geoviews as gv
import holoviews as hv
import hvplot.pandas
import hvplot.xarray
import pandas as pd
import requests
# import matplotlib.pyplot as plt
import rioxarray as rxr
import rioxarray.merge as rxrmerge
import xarray as xr

In [2]:
grasslands_url = (
    "https://data.fs.usda.gov/geodata/edw/edw_resources/shp"
    "/S_USA.NationalGrassland.zip")
grasslands_gdf = gpd.read_file(grasslands_url)
grasslands_gdf

NATIONALGR                            GRASSLANDN    GIS_ACRES  \
0   295509010328           Sheyenne National Grassland    70428.175   
1   295520010328    Little Missouri National Grassland  1025313.868   
2   295513010328      Thunder Basin National Grassland   626249.208   
3   295521010328             Oglala National Grassland   215804.927   
4   295519010328      Crooked River National Grassland   173593.026   
5   295515010328              Caddo National Grassland    68479.549   
6   295523010328             Pawnee National Grassland   208424.885   
7   295522010328           Comanche National Grassland   444413.904   
8   295524010328           Cimarron National Grassland   109101.348   
9   295508010328              Kiowa National Grassland   144281.321   
10  295511010328       Black Kettle National Grassland    33103.349   
11  295512010328        Rita Blanca National Grassland    94127.091   
12  295514010328    McClellan Creek National Grassland     1401.715   
13  295525010328             Curlew National Grassland    74783.572   
14  295517010328        Grand River National Grassland   154665.301   
15  295510010328        Cedar River National Grassland     6717.517   
16  281771010328        Fort Pierre National Grassland   209044.225   
17  295518010328        Buffalo Gap National Grassland   654877.177   
18  295507010328       Butte Valley National Grassland    19489.170   
19  295516010328  Lyndon B. Johnson National Grassland   115408.461   

    SHAPE_AREA  SHAPE_LEN                                           geometry  
0     0.033356   4.097398  MULTIPOLYGON (((-97.31081 46.51457, -97.30559 ...  
1     0.492746  60.420702  MULTIPOLYGON (((-104.01688 47.51793, -104.0115...  
2     0.282888  44.088050  MULTIPOLYGON (((-105.46005 43.31908, -105.4601...  
3     0.096279   1.970612  POLYGON ((-103.72477 43.00100, -103.72007 43.0...  
4     0.079499   2.815873  POLYGON ((-120.98025 44.72935, -120.98030 44.7...  
5     0.026940   1.159342  MULTIPOLYGON (((-95.85492 33.79814, -95.85494 ...  
6     0.089972  15.341594  MULTIPOLYGON (((-104.58106 40.82664, -104.5810...  
7     0.183064  26.658022  MULTIPOLYGON (((-104.02263 37.69224, -104.0225...  
8     0.044765   5.539623  MULTIPOLYGON (((-101.98977 37.11933, -101.9852...  
9     0.058543   9.858642  MULTIPOLYGON (((-104.30414 36.08063, -104.3041...  
10    0.013340   4.561060  MULTIPOLYGON (((-99.91659 35.71892, -99.91661 ...  
11    0.038271   6.652113  MULTIPOLYGON (((-102.62986 36.44806, -102.6254...  
12    0.000562   0.115902  POLYGON ((-100.86003 35.20951, -100.86008 35.2...  
13    0.032983   1.771642  MULTIPOLYGON (((-112.69950 42.24750, -112.6995...  
14    0.072336   9.796405  MULTIPOLYGON (((-102.08142 45.68619, -102.0814...  
15    0.003157   0.999947  MULTIPOLYGON (((-101.82221 45.95896, -101.8170...  
16    0.095149   1.455518  POLYGON ((-100.08409 44.28162, -100.08409 44.2...  
17    0.295196  33.006274  MULTIPOLYGON (((-102.33839 43.93678, -102.3383...  
18    0.008557   0.853736  MULTIPOLYGON (((-121.99600 41.84049, -121.9960...  
19    0.045238   1.177130  POLYGON ((-97.67964 33.43396, -97.67951 33.433...

In [ ]:
# Index of /POLARIS/PROPERTIES/v1.0/ph/mean/60_100
# Change it according to chosen grassland units 
# (unit might not fit into one tile: 
# load in more than one tile per grassland 
# and need to merge with rioxarray (greenspace assignment)
# Download data and load it back again (ndvi assignment)

# Probably I need a function since I have two different 
# set of min values and two climate variables for each (4 runs)

polaris_das = []
for min_lat in [45, 46]:
    min_lon =-102
    max_lat, max_lon = min_lat+1, min_lon+1
    polaris_url_format = (
        "http://hydrology.cee.duke.edu/POLARIS/PROPERTIES/v1.0"
        "/ph/mean/60_100/lat{min_lat}{max_lat}_lon{min_lon}{max_lon}.tif"
    )

    polaris_url = polaris_url_format.format(
        min_lat=min_lat, min_lon=min_lon, max_lat=max_lat, max_lon=max_lon)
    polaris_das.append(
        rxr.open_rasterio(polaris_url, masked=True).squeeze())
    
ph_da = rxrmerge.merge_arrays(polaris_das)
ph_da

# check crs

In [14]:
# https://lpdaac.usgs.gov/products/srtmgl1v003/
# Elevation data

cedar_river_gdf = (
    grasslands_gdf
    .set_index('GRASSLANDN')
    .loc[['Cedar River National Grassland']]
)

# might be the looping variable
download_key ='Cedar-River-SRTM'

srtm_downloader = eaapp.AppeearsDownloader(
    download_key = download_key,
    product='SRTMGL1_NC.003',
    layer='SRTMGL1_DEM',
    start_date='02-11-2000',
    end_date='02-21-2000',
    polygon=cedar_river_gdf)
srtm_downloader.download_files()

In [53]:
srtm_paths = glob(
    os.path.join(
        srtm_downloader.data_dir,
        'SRTMGL1_NC.003*',
        '*.tif')
)

srtm_da = rxrmerge.merge_arrays(
    [rxr.open_rasterio(srtm_path, masked=True).squeeze()
     for srtm_path
     in srtm_paths])

# check crs


In [29]:
maca_url = (
    "http://thredds.northwestknowledge.net:8080/thredds/ncss"
    "/agg_macav2metdata_pr_CCSM4_r6i1p1"
    "_historical_1950_2005_CONUS_monthly.nc"
    "?var=precipitation"
    "&?disableLLSubset=on"
    "&disableProjSubset=on"
    "&horizStride=1"
    "&time_start=1980-01-15T00%3A00%3A00Z"
    "&time_end=1980-12-15T00%3A00%3A00Z"
    "&timeStride=1&accept=netcdf"
)

maca_response = requests.get(maca_url)

# cotext magager
with open('maca.nc', 'wb') as maca_file:
    maca_file.write(maca_response.content)

:DynamicMap   []
   :Image   [lon,lat]   (precipitation)

In [54]:
maca_ds = xr.open_dataset('maca.nc')
# Reassign coordinates
maca_ds = maca_ds.assign_coords(lon=maca_ds.lon-360)

# Pull out precipitation variable to work with dataarray
precip_da = maca_ds.precipitation

#Directly write the crs
precip_da.rio.write_crs("epsg:4326", inplace=True)

# Set the spatial dimensions
precip_da.rio.set_spatial_dims('lon', 'lat', inplace=True)

precip_da.mean('time').hvplot(rasterize=True) * cedar_river_gdf.hvplot()

:DynamicMap   []
   :Overlay
      .Image.I    :Image   [lon,lat]   (precipitation)
      .Polygons.I :Polygons   [x,y]

In [39]:
cedar_river_gdf.total_bounds

array([-101.86375707,   45.9441578 , -101.23001608,   46.07444448])

In [49]:
precip_da.rio.clip(cedar_river_gdf.geometry)

precip_da.rio.clip_box(*cedar_river_gdf.total_bounds).mean('time').hvplot()

:Image   [lon,lat]   (precipitation)